In [1]:
#!pip install requests
#!pip install beautifulsoup4

In [1]:
import pandas as pd
import numpy as np
import requests
import urllib
import re
from bs4 import BeautifulSoup
import bs4

In [2]:
import os
currentPath = os.getcwd()
print(currentPath)

C:\Users\ohike\VS Code\bigkinds_crawler


In [3]:
df_news = pd.read_excel(r'E:\내 드라이브\greenwashing_company\consolidated\df_news_esgkeywords.xlsx')

In [4]:
df_news

Unnamed: 0        뉴스 식별자        일자     언론사  기고자  \
0              28  2.100101e+06  20220505    매일경제  진영화   
1              52  2.100601e+06  20220202    한국경제  NaN   
2              90  2.100101e+06  20211013    매일경제  김효혜   
3              93  1.100401e+06  20210927    동아일보  NaN   
4              94  1.100901e+06  20210927    중앙일보  NaN   
...           ...           ...       ...     ...  ...   
10011      705277  1.100401e+06  20200728    동아일보  김민범   
10012      705278  7.101201e+06  20200728  디지털타임스  김아름   
10013      705279  2.100101e+06  20200728    매일경제  신미진   
10014      705290  7.100501e+06  20200507    전자신문  이주현   
10015      705672  2.100101e+06  20190109    매일경제  NaN   

                                            제목    통합 분류1          통합 분류2  \
0                        신세계푸드 식물성 원료 베이커리 신제품     지역>경남           사회>여성   
1                       기고 대체육 K택소노미 핵심으로 육성해야  경제>산업_기업        경제>취업_창업   
2               생수도 에코 프리미엄이 대세 신세계푸드 저스트워터 인기     경제>유통          경제>자동차   
3                          원두 찌꺼기 활용한 버섯 재배 키트   경제>경제일반             NaN   
4                  Biz  Now 커피찌꺼기로 친환경 버섯 키우세요     지역>전남           지역>경남   
...                                        ...       ...             ...   
10011  동원산업 친환경 노르웨이 양식 스타트업에 65억원 투자 지분 97 확보    경제>반도체        경제>취업_창업   
10012             동원산업 노르웨이 연어 양식 스타트업에 65억 투자    경제>반도체        경제>취업_창업   
10013             동원산업 노르웨이 연어 양식 스타트업에 65억 투자     지역>울산           경제>무역   
10014        필환경 기업 동원산업 수산물 보냉재 친환경 아이스팩으로 대체  경제>산업_기업         사회>사회일반   
10015                 톡톡 이상품 휴럼  잇트루 유기농양배추케일즙  경제>산업_기업   IT_과학>IT_과학일반   

        통합 분류3 사건/사고 분류1  ...  \
0        지역>충남       NaN  ...   
1          NaN       NaN  ...   
2          NaN       NaN  ...   
3          NaN       NaN  ...   
4        지역>강원       NaN  ...   
...        ...       ...  ...   
10011   경제>자동차       NaN  ...   
10012   경제>자동차       NaN  ...   
10013    지역>경남       NaN  ...   
10014    지역>충남       NaN  ...   
10015   경제>자동차       NaN  ...   

                                                     키워드  \
0      신세계푸드,식물,원료,베이커리,신세계푸드,건강,특수식,전문,기업,닥터,키친,건강,식...   
1      택소,노미,핵심,육성,환경부,경제,활동,원칙,기준,제시,한국,녹색,분류,체계,K택소...   
2      생수,에코,프리미엄,대세,신세계푸드,저스트워터,인기,플라스틱,사용,무라벨,패키지,적...   
3      활용,원두,찌꺼기,키트,버섯,재배,본점,서울,중구,신세계백화점,베키아에누보,이탈리안...   
4      커피찌꺼기,버섯,신세계백화점,베키아에누보,이탈리안,레스토랑,커피박,커피찌꺼기,버섯,...   
...                                                  ...   
10011  동원산업,노르웨이,양식,스타트업,65억,투자,확보,지분,9.7%,노르웨이,에볼루션,...   
10012  동원산업,노르웨이,연어,양식,스타트업,투자,양식,동원산업은이,양식,보유,노르웨이,스...   
10013  동원산업,노르웨이,연어,양식,스타트업,투자,동원산업,확대,대서양,연어,수입,경로,동...   
10014  환경,기업,동원산업,수산물,보냉재,아이스팩,대체,동원산업,보냉재,수산물,포장,100...   
10015  휴럼,잇트루,유기농,양배,추케,일즙,휴럼,건강,식품,전문,기업,대표,김진석,잇트루,...   

                                       특성추출(가중치순 상위 50개)  \
0      마들렌,식물성,단호박,통호밀,신세계푸드,2종,비건,특수식,밀가루,버개스,에코,통곡물...   
1      대체육,일회용품,소비자,대체가공식품,지침서,뒷받침,녹색분류체계,택소,메탄가스,esg...   
2      저스트워터,신세계푸드,친환경,에코,스미스,소비자,sns,영화배우,판매량,온라인,가치...   
3      신세계푸드,키트,서울,신세계백화점,커피박,중구,베키아에누보,찌꺼기,버섯,이탈리안,레...   
4      키트,신세계푸드,커피찌꺼기,베키아에누보,커피박,신세계백화점,버섯,레스토랑,이탈리안,...   
...                                                  ...   
10011                  노르웨이,동원산업,양식장,대서양,스타트업,새먼,수산업,65억   
10012  양식장,노르웨이,동원산업,새먼,대서양,수산업,65억,동원산업은이,스타트업,지속가능,...   
10013  동원산업,대서양,노르웨이,양식장,새먼,65억,스타트업,수산업,양식업,몰데,지속가능,...   
10014  동원산업,아이스팩,수산물,보냉재,재활용,종이팩,하수구,경량화,환경오염,물청소,불가능...   
10015  잇트루,휴럼,건강식품,양배,유기가공식품,이지컷,추케일즙,추즙,양배추케일즙,양배추즙,...   

                                                      본문  \
0      신세계푸드가 건강 특수식 전문기업 닥터키친과 함께 개발한 건강 식빵 2종과 친환경 ...   
1      지난해 말 환경부가 친환경 경제활동의 원칙과 기준을 제시한 한국형 녹색분류체계K택소...   
2      플라스틱 사용을 줄이고 무라벨 친환경 패키지 등을 적용해 친환경적 가치를 담은 에코...   
3      26일 서울 중구 신세계백화점 본점 내 이탈리안 레스토랑 베키아에누보에서 신세계푸드...   
4      신세계백화점이 이탈리안 레스토랑 베키아에누보에서 커피박커피찌꺼기으로 만든 친환경 버...   
...                                                  ...   
10011  동원산업은 친환경 양식 기술을 보유한 노르웨이의 연어 양식 스타트업 새먼 에볼루션S...   
10012  디지털타임스 김아름 기자 동원산업은이 필환경 양식 기술을 보유한 노르웨이의 연어 양...   
10013  동원산업이 대서양 연

In [65]:
#Uncomment to export the original dataframe into the excel format
#df_news.to_excel("output.xlsx")

In [5]:
#Drop unnecessary column & Change column name
df_news = df_news.drop(['Unnamed: 0'], axis=1)
df_news.columns = df_news.columns.str.replace('본문', '본문 미리보기')

In [6]:
#Set as :20 to make a small sample
df_news = df_news.iloc[:]

In [7]:
pd.set_option('display.max_colwidth', None)
df_news['URL'].astype(str)
df_news['URL'].fillna('NaN')

0                                 http://news.mk.co.kr/newsRead.php?no=399849&year=2022
1                                https://www.hankyung.com/opinion/article/2022020270981
2                                 http://news.mk.co.kr/newsRead.php?no=970300&year=2021
3                           https://www.donga.com/news/article/all/20210926/109424227/1
4                                           https://www.joongang.co.kr/article/25009809
                                              ...                                      
10011                       https://www.donga.com/news/article/all/20200728/102201130/1
10012    http://www.dt.co.kr/contents.html?article_no=2020072802109932060007&ref=jeadan
10013                             http://news.mk.co.kr/newsRead.php?no=769135&year=2020
10014                                              http://www.etnews.com/20200507000094
10015                              http://news.mk.co.kr/newsRead.php?year=2019&no=16337
Name: URL, Length: 10016, dtype:

In [8]:
print(df_news['URL'])

0                                 http://news.mk.co.kr/newsRead.php?no=399849&year=2022
1                                https://www.hankyung.com/opinion/article/2022020270981
2                                 http://news.mk.co.kr/newsRead.php?no=970300&year=2021
3                           https://www.donga.com/news/article/all/20210926/109424227/1
4                                           https://www.joongang.co.kr/article/25009809
                                              ...                                      
10011                       https://www.donga.com/news/article/all/20200728/102201130/1
10012    http://www.dt.co.kr/contents.html?article_no=2020072802109932060007&ref=jeadan
10013                             http://news.mk.co.kr/newsRead.php?no=769135&year=2020
10014                                              http://www.etnews.com/20200507000094
10015                              http://news.mk.co.kr/newsRead.php?year=2019&no=16337
Name: URL, Length: 10016, dtype:

In [9]:
df_news

뉴스 식별자        일자     언론사  기고자  \
0      2.100101e+06  20220505    매일경제  진영화   
1      2.100601e+06  20220202    한국경제  NaN   
2      2.100101e+06  20211013    매일경제  김효혜   
3      1.100401e+06  20210927    동아일보  NaN   
4      1.100901e+06  20210927    중앙일보  NaN   
...             ...       ...     ...  ...   
10011  1.100401e+06  20200728    동아일보  김민범   
10012  7.101201e+06  20200728  디지털타임스  김아름   
10013  2.100101e+06  20200728    매일경제  신미진   
10014  7.100501e+06  20200507    전자신문  이주현   
10015  2.100101e+06  20190109    매일경제  NaN   

                                            제목    통합 분류1          통합 분류2  \
0                        신세계푸드 식물성 원료 베이커리 신제품     지역>경남           사회>여성   
1                       기고 대체육 K택소노미 핵심으로 육성해야  경제>산업_기업        경제>취업_창업   
2               생수도 에코 프리미엄이 대세 신세계푸드 저스트워터 인기     경제>유통          경제>자동차   
3                          원두 찌꺼기 활용한 버섯 재배 키트   경제>경제일반             NaN   
4                  Biz  Now 커피찌꺼기로 친환경 버섯 키우세요     지역>전남           지역>경남   
...                                        ...       ...             ...   
10011  동원산업 친환경 노르웨이 양식 스타트업에 65억원 투자 지분 97 확보    경제>반도체        경제>취업_창업   
10012             동원산업 노르웨이 연어 양식 스타트업에 65억 투자    경제>반도체        경제>취업_창업   
10013             동원산업 노르웨이 연어 양식 스타트업에 65억 투자     지역>울산           경제>무역   
10014        필환경 기업 동원산업 수산물 보냉재 친환경 아이스팩으로 대체  경제>산업_기업         사회>사회일반   
10015                 톡톡 이상품 휴럼  잇트루 유기농양배추케일즙  경제>산업_기업   IT_과학>IT_과학일반   

        통합 분류3 사건/사고 분류1 사건/사고 분류2  ...  \
0        지역>충남       NaN       NaN  ...   
1          NaN       NaN       NaN  ...   
2          NaN       NaN       NaN  ...   
3          NaN       NaN       NaN  ...   
4        지역>강원       NaN       NaN  ...   
...        ...       ...       ...  ...   
10011   경제>자동차       NaN       NaN  ...   
10012   경제>자동차       NaN       NaN  ...   
10013    지역>경남       NaN       NaN  ...   
10014    지역>충남       NaN       NaN  ...   
10015   경제>자동차       NaN       NaN  ...   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              키워드  \
0                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                           신세계푸드,식물,원료,베이커리,신세계푸드,건강,특수식,전문,기업,닥터,키친,건강,식빵,2종,패키지,활용,세트,마들렌,출시,웰니스,wellness,콘셉트,베이커리,제품,라인업,확대,5일,신세계푸드,식물성,단호박,식빵,식빵,곤약,통곡물,2종,식물성,단호박,식빵,동물,원료,지양,트렌드,비건,소비,버터,우유,달걀,식물,원료,사용,제품,단호박,건강,단맛,탕종,방식,일반,식빵,식감,식빵,곤약,통곡물,곤약,곡물,통밀,대두,통호밀,해바라기,보리,귀리,대두,옥수수,아마,식빵,곤약,밀가루,마들렌,버개스,펄프,용기,소재,에코,디저트,마들렌,출시,버개스,펄프,소재,사탕수수,설탕액,섬유소,재질,종이   
1      택소,노미,핵심,육성,환경부,경제,활동,원칙,기준,제시,한국,녹색,분류,체계,K택소노미,지침서,택소노미,taxonomy,유럽연합,EU,녹색,정의,ESG,환경,사회,지배구조,투자,정보,공개,원활,규정,가지,환경,가지,충족,지속가능,활동,정부,자본,흐름,녹색,투자,녹색,금융,유도,기후,위기,대응,사회,실질,전환,활동,인증,녹색분류체계,금융회

In [10]:
# Loop through URLs, scrap information, identify the main body
# URL이 주어졌을 경우 해당 매체 웹사이트로부터 뉴스기사전문 크롤링

#최종결과물에 대한 텍스트 전처리-불용어 제거
#반복적인 불용어에 대한 메뉴얼 수정 내용 추가 - 미디어 매채별 예외처리 등록
def clean_html(raw_html):
    cleanr = re.compile('<.*?>|\s{2}|\n')
#    cleanr = re.compile('[^-가-힣a-zA-Z0-9/ ]')
    clean_text = re.sub(cleanr, '', raw_html)
    clean_text = clean_text.replace('window.jQuery || document.write("")', '')
    clean_text = clean_text.replace('Copyright ⓒ 동아일보 &amp; donga.com', '') #동아일보
    clean_text = clean_text.replace('좋아요 이미지좋아요슬퍼요 이미지슬퍼요화나요 이미지화나요후속기사 원해요 이미지후속기사 원해요기사추천 이미지기사추천공유 이미지공유공유하기닫기', '')
    clean_text = clean_text.replace('ⓒ 매일경제 &amp; mk.co.kr', '').replace('googletag.display("google_dfp_MC_250x250")', '').replace('googletag.display("google_dfp_MC_2x1,fluid")', '')
    clean_text = clean_text.replace('[', '').replace(']', '').replace('&amp', '').replace(', ■', '').replace('■ &lt', '').replace(';', '').replace('◆', '').replace('▲', '').replace('◇', '').replace('⊙', '')
    return clean_text


def crawling_main_text(url):
        
        if type(url)==float:
            content = 'n/a'
        
        
        #조선일보 - 미완성
        elif 'chosun' in url:
            url = requests.get(url, headers={'User-Agent':'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.88 Safari/537.36'})

            soup = BeautifulSoup(url.text, "html.parser", from_encoding='utf-8')
            content_obj = soup.find_all("div", class_="article-body")
            
            
            content = clean_html(str(content_obj))
        
        
        #중앙일보
        elif 'joins' in url:
            url = requests.get(url, headers={'User-Agent':'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.88 Safari/537.36'})

            soup = BeautifulSoup(url.text, "html.parser", from_encoding='utf-8')

            content_obj = soup.find_all('div', class_="article_body")
            content = clean_html(str(content_obj))
        
        
        #동아일보
        elif 'donga' in url:
            url = requests.get(url, headers={'User-Agent':'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.88 Safari/537.36'})

            soup = BeautifulSoup(url.text, "html.parser", from_encoding='utf-8')

            content_obj = soup.find_all('div', class_="article_txt")
            content = clean_html(str(content_obj))
        
        
        #한겨례신문
        elif 'hani' in url:
            url = urllib.request.Request(url, headers={'User-Agent':'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.88 Safari/537.36'})
            res = urllib.request.urlopen(url).read().decode("utf-8")
    
            soup = BeautifulSoup(res, "html.parser", from_encoding='utf-8')
            
            content_obj = soup.find_all('div', class_="text")
            content = clean_html(str(content_obj))
        

        #경향신문
        elif 'khan' in url:
            url = requests.get(url, headers={'User-Agent':'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.88 Safari/537.36'})

            soup = BeautifulSoup(url.text, "html.parser", from_encoding='utf-8')

            content_obj = soup.find_all('p', class_="content_text")
            content = clean_html(str(content_obj))
        
        
        #한국경제
        elif 'hankyung' in url:
            try: 
                url = urllib.request.Request(url, headers=headers)
                res = urllib.request.urlopen(url).read().decode("utf-8")
    
                soup = BeautifulSoup(res, "html.parser")
    
                content_obj = soup.find_all('div', id="articletxt")
                content = clean_html(str(content_obj))
            except:
                pass

            
        #매일경제
        elif 'mk' in url:
            url = requests.get(url, headers={'User-Agent':'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.88 Safari/537.36'})

            soup = BeautifulSoup(url.text, "html.parser", from_encoding='utf-8')
            soup_alt = bs4.BeautifulSoup(url.content.decode('euc-kr', 'replace'), "html.parser")

            content_obj = soup_alt.find_all('div', class_="art_txt")

            content = clean_html(str(content_obj))
        
        #KBS
        elif 'kbs' in url:
            url = requests.get(url, headers={'User-Agent':'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.88 Safari/537.36'})
            
            soup = BeautifulSoup(url.text, "html.parser", from_encoding='utf-8')
            
            content_obj = soup.find_all('div', id="cont_newstext")
            content = clean_html(str(content_obj))
        
        #MBC
        elif 'imbc' in url:
            url = requests.get(url, headers={'User-Agent':'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.88 Safari/537.36'})
            
            soup = BeautifulSoup(url.text, "html.parser", from_encoding='utf-8')
            
            content_obj = soup.find('div', {'itemprop' : 'articleBody'})
            content = clean_html(str(content_obj))
        
        #OBS
        elif 'obsnews' in url:
            url = requests.get(url, headers={'User-Agent':'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.88 Safari/537.36'})
            
            soup = BeautifulSoup(url.text, "html.parser", from_encoding='utf-8')
            
            content_obj = soup.find_all('article', id="article-view-content-div")
            content = clean_html(str(content_obj))
        
        #SBS
        elif 'sbs' in url:
            url = requests.get(url, headers={'User-Agent':'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.88 Safari/537.36'})
            
            soup = BeautifulSoup(url.text, "html.parser", from_encoding='utf-8')
            
            content_obj = soup.find('div', {'itemprop' : 'articleBody'})
            content = clean_html(str(content_obj))
        
        #YTN
        elif 'ytn' or 'yonhap' in url:
            url = requests.get(url, headers={'User-Agent':'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.88 Safari/537.36'})
            
            soup = BeautifulSoup(url.text, "html.parser", from_encoding='utf-8')
            
            main_article = soup.find('div', {'itemprop' : 'articleBody'})
            if main_article == None:
                main_article = soup.find('div', {'class' : 'article=txt'})
                
            content = clean_html(str(main_article))
        
    
        return content
                                     

In [11]:
#For Loop을 통한 본문 크롤링
#데이터 프레임에 추가

df_news['main_content']='n/a'

for i, url in enumerate(df_news['URL']):
    print(url)
    print(type(url))
    try:
        main_body = crawling_main_text(url)
        print(main_body)
        df_news['main_content'].iloc[i] = main_body
    except:
        continue
    

http://news.mk.co.kr/newsRead.php?no=399849&year=2022
<class 'str'>


C:\Users\ohike\anaconda3\lib\site-packages\bs4\__init__.py:226: UserWarning: You provided Unicode markup but also provided a value for from_encoding. Your from_encoding will be ignored.
  warnings.warn("You provided Unicode markup but also provided a value for from_encoding. Your from_encoding will be ignored.")


진영화 기자, 무단전재 및 재배포 금지	


C:\Users\ohike\AppData\Local\Temp\ipykernel_23824\3124228257.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_news['main_content'].iloc[i] = main_body


https://www.hankyung.com/opinion/article/2022020270981
<class 'str'>
http://news.mk.co.kr/newsRead.php?no=970300&year=2021
<class 'str'>
신세계푸드 관계자는 "친환경에 대한 사회적 관심이 높아지고 지속 가능한 소비를 중시하는 소비자들의 트렌드를 고려해 저스트워터를 선보이고 있다"며 "더불어 주요 소비층인 MZ세대들이 가치소비를 중요하게 생각하는 만큼 이들의 니즈를 충족시키기 위한 제품과 활동을 지속적으로 선보일 것"이라고 말했다.김효혜 기자, 무단전재 및 재배포 금지	
https://www.donga.com/news/article/all/20210926/109424227/1
<class 'str'>
26일 서울 중구 신세계백화점 본점 내 이탈리안 레스토랑 ‘베키아에누보’에서 신세계푸드 직원들이 커피박(원두 찌꺼기)으로 만든 친환경 버섯 재배 키트를 소개하고 있다. 신세계푸드 제공 #신세계백화점#베키아에누보#버섯 
https://www.joongang.co.kr/article/25009809
<class 'str'>
커피찌꺼기로 친환경 버섯 키우세요신세계백화점이 이탈리안 레스토랑 ‘베키아에누보’에서 커피박(커피찌꺼기)으로 만든 친환경 버섯 재배 키트를 증정한다고 26일 밝혔다. 신세계푸드 직원들이 친환경 버섯 재배 키트를 소개하고 있다. 사진 신세계푸드 
http://news.mk.co.kr/newsRead.php?no=916285&year=2021
<class 'str'>
현대백화점면세점은 면세 업계에서는 처음으로 다음달 1일부터 비닐 포장재를 모두 종이 소재로 바꾼다. 소위 '뽁뽁이'로 불리는 완충캡과 테이프 등 포장재도 모두 종이로 교체한다.비닐 완충캡은 종이 소재 완충재로 교체하며, 비닐 테이프는 전분을 접착제로 사용하는 종이 테이프를 사용한다. 모두 종이 소재로 분리배출이 가능하다. 신세계푸드는 고객과 자원 재사용의 중요성을 공유하기 위해 커피 찌

...

이유섭 기자, 무단전재 및 재배포 금지	선형 디자인 천장과 선반을 통해 탑승객에게 넉넉하고 편안한 공간과 느낌을 제공한다. 다양한 색상의 발광 다이오드(LED) 조명도 객실에 설치, 이륙·일몰·일출·영화감상·수면·착륙 등 상황에 맞춰 다양한 객실 분위기를 연출할 수 있다. 대한항공은 737-8에 프레스티지클래스 8석, 이코노미클래스 138석을 배치했다.다.실시했다.
http://www.mk.co.kr/economy/view/2022/130106
<class 'str'>

http://news.mk.co.kr/newsRead.php?no=125115&year=2022
<class 'str'>
문광민 기자, 무단전재 및 재배포 금지	대비 수소 도입이 늦은 항공업계와 공항 시설의 수소 공급과 인프라 구축 체계를 마련하기 위한 상징적인 출발점"이라며 "대한항공은 앞으로도 탄소중립과 한국 수소경제 활성화에 적극 기여할 것"이라고 말했다.스는 한국 지역 수소 항공기 수요 분석을, 에어리퀴드는 항공업계 수소연료 도입 로드맵 구축을 맡는다. 대한항공은 지난 9일 인천국제공항공사, 에어버스 코리아, 에어리퀴드 코리아 등과 '항공업계와 공항의 수소 공급과 인프라 개발을 위한 업무협약'을 맺었다고 10일 밝혔다.
http://www.hani.co.kr/arti/economy/marketing/1030520.html
<class 'str'>
왼쪽부터 기욤 코테 에어리퀴드코리아 대표, 파브리스 에스피노자 에어버스코리아 대표, 전형욱 인천공항공사 인프라본부장, 이수근 대한항공 안전보건 총괄 부사장. 대한항공 제공대한항공이 수소 연료 항공기 시대를 대비해 인프라 구축에 나선다.대한항공은 지난 9일 오후 인천국제공항공사, 에어버스코리아, 에어리퀴드코리아와 ‘항공업계와 공항의 수소 공급 및 인프라 개발을 위한 업무협약’을 맺었다고 10일 밝혔다.이번 협약은 글로벌 항공기 제작업체 에어버스가 2035년까지 수소 연료 항공기를 상용화할 계획이라고 밝힌데 따른 것이다. 협약은 각사가 미래 수소 

강달호 현대오일뱅크 사장(오른쪽)과 우기홍 대한항공 사장(왼쪽)이 서울 강서구 대한항공 본사에서 바이오 항공유 생태계 구축을 위한 업무협약을 체결했다. 사진 현대오일뱅크 현대오일뱅크가 대한항공과 손잡고 친환경 바이오 항공유 시장 개척에 나선다. 양사는 바이오 항공유 제조 및 사용 기반 조성 협력을 위한 양해각서를 30일 체결했다. 양사는 향후 국내 바이오 항공유 제조·사용 기반 조성, 바이오 항공유 사용을 위한 시장조사 및 연구개발 등을 함께 진행할 계획이다. 현재 세계 바이오 항공유 사용량은 연간 2만~3만t으로 전체 항공유 중 0.1%에 불과하다. 국제에너지기구는 2040년 바이오 항공유 수요가 연간 6000만t까지 증가할 것으로 전망한다. 
https://www.hankyung.com/economy/article/2021063053651
<class 'str'>
https://www.donga.com/news/article/all/20210630/107721707/1
<class 'str'>
바이오항공유 생태계 구축 위한 업무협약 체결탄소중립 위해 바이오항공유 관련 협력 체계 구축바이오항공유, 곡물·동물성 지방 등으로 만든 연료탄소배출 최대 80%↓ 기대바이오항공유 상용화·사업기회 발굴대한항공이 항공부문 기후 변화에 적극 대응하기 위해 현대오일뱅크와 협력하기로 했다.대한항공은 30일 서울시 강서구 소재 본사에서 현대오일뱅크와 ‘바이오항공유 생태계 구축을 위한 업무협약(MOU)’을 체결했다. 체결식에는 우기홍 대한항공 사장과 강달호 현대오일뱅크 사장 등 주요 관계자들이 참석했다.이번 협력은 항공부문 기후변화 주요 대응 수단으로 바이오항공유 사용이 강조되는 추세에 따라 이뤄졌다고 한다. 바이오항공유 상용화와 관련 사업기회 발굴이 주요 목적이다. 바이오항공유는 곡물이나 식물, 해조류, 동물성 지방 등을 원료로 하는 연료다. 기존 항공유 대비 탄소배출을 최대 80%까지 감축할 수 있는 것으로 전해진다. 다만 3배 이상 높은 가격과 관련 인프라가 부족해 상용화에 

http://news.mk.co.kr/newsRead.php?year=2019&no=1024035
<class 'str'>
디지털뉴스국 조성신 기자, 무단전재 및 재배포 금지	수익을 올리는 부가가치사업은 아니지만, 전 세계에 지역을 알리는 좋은 기회가 될 수 있다"면서 "경기 침체의 골이 깊은 지역경제에 활기를 불어 넣는 계기가 될 수 있을 것으로 확신한다"고 말했다.갖추고 있다.부산시는 부산방문 전지훈련팀을 위한 수준별·종목별 훈련시설, 숙박시설, 훈련파트너, 의료기관 매칭 등 논스톱 패키지 서비스(Non-stop Package Service)를 구축했다. 전지훈련 유치 홍보 홈페이지를 한국어·영어 두 가지 버전으로 제작해 서비스를 시작했으며, 지난달 15일에는 부산대병원 등 13개 지역병원들과 전지훈련팀 유치 및 의료편의 향상을 위해 유기적으로 협조한다는 내용의 업무협약식도 체결했다. 이와 함께 삼척(핸드볼)과 진주(배드민턴), 삼천포(농구) 등지도 지역별 특화된 종목의 각국 올림픽 대표팀 전지훈련지 유치를 위해 팔을 걷어 부쳤다.한 500명 이상의 인원이 양산실내체육관에서 훈련과 친선경기 등에 참여할 예정이다. 양산시는 전지훈련장 운영과 관련한 각급 방문자까지 더하면 1000명 이상이 양산을 다녀갈 것으로 추산하고, 양산을 알리는 홍보 효과는 물론, 음식업와 숙박업 등 지역 소상공업소의 경기 활성화에 적잖이 기여할 것으로 기대하고 있다. 싱가포르 사격 국가대표팀은 도쿄올림픽 대비 현지적응을 위한 전지훈련지로 2014 아시안게임을 개최한 인천시를 선택했다. 이들 대표팀은 지난 10월 24일부터 5일간 미니 전지훈련을 마치고 돌아갔다. 싱가포르 사격대표팀은 도쿄올림픽을 앞두고 또다시 인천시를 찾아서 훈련을 할 예정이며, 6개국의 태권도 전지훈련단도 인천을 찾아 현지 적응훈련에 돌입할 계획인 것으로 알려졌다.
https://www.hankyung.com/economy/article/201910184730g
<class 'str'>
http://news.mk.c

대전시가 도입해 6일 운행을 시작한 수소버스. 대전시 제공대전도 대중교통 수소버스 시대를 열었다.대전시와 계룡교통은 지난 6일부터 수소버스 2대를 613번(비래동~갈마아파트), 615번(대한통운~정림동) 노선에서 운행하고 있다고 8일 밝혔다. 시는 수소차량이 내연기관차들과 달리 이산화탄소 등 대기오염물질을 배출하지 않고 대기 중 미세먼지가 포함된 산소를 정화하는 장점이 있어 도입했다고 설명했다.시는 앞으로 2025년까지 해마다 사용 연한이 도래하는 시내버스 가운데 20여대 씩을 친환경 수소버스로 교체하고, 현재 705대 정도인 수소차를 내년까지 1100여대 수준으로 늘려나갈 방침이다. 이를 위해 시는 대덕구 신대동 버스공영차고지에 국비 42억원과 시비 18억원을 들여 수소충전소를 설치했다. 이 충전소는 연면적 367㎡에 충전설비 2기 갖췄으며 대전도시공사가 새벽 4~자정까지 연중무휴로 운영한다. 이 곳은 시간당 60㎏을 충전할 수 있어 1일 버스(29㎏) 40대, 승용차(5㎏) 240대를 충전할 수 있다. 시는 현재 5곳인 수소충전소도 내년까지 10곳으로 늘릴 계획이다.허태정 대전시장은 “기후변화 위기를 벗어나려면 탄소중립 사회로 가는 에너지·산업 정책을 적극적으로 시행해야 한다. 수소 차량 보급, 수소산업 육성 정책을 적극적으로 추진하겠다”고 말했다.송인걸 기자 igsong@hani.co.kr
https://www.khan.co.kr/local/Daejeon/article/202111081002011
<class 'str'>
대전에서도 친환경 수소버스 달린다., 대전시는 친환경 수소 에너지 사용을 확대하기 위해 시내버스공영차고지 안에 수소버스충전소를 구축한 뒤 수소버스 2대를 시내버스 노선에 본격 투입했다고 8일 밝혔다., 수소버스는 비래동~갈마아파트 구간을 운행하는 613번 노선과 대한통운~정림동 구간을 오가는 615번 노선에 각각 1대씩 배차됐다. 대전시 관계자는 “지난 6일부터 수소버스를 노선에 투입했다”면서 “올해 안에 12대까지 늘릴 예정”이라고 밝

CJ대한통운 관계자는 "최근 미세먼지, 플라스틱 등 환경문제가 세계적으로 대두되는 가운데 친환경을 넘어 반드시 환경을 보호해야 하는 필환경 바람이 불고 있다"며 "글로벌 종합물류기업으로서 환경문제에 선도적으로 대응하고 필환경을 실천하는데 앞장서겠다"고 말했다.이상규 기자 boyondal@mkinternet.com, 무단전재 및 재배포 금지	UN SDGs협회, 아트임팩트와 함께 지속가능경영 확산과 지구환경보호를 위한 '플라스틱 이니셔티브' 업무협약을 체결했다고 15일 밝혔다.
http://news.mk.co.kr/newsRead.php?year=2019&no=1014423
<class 'str'>
김효혜 기자, 무단전재 및 재배포 금지	으로도 시민 편익을 위해 지하철을 이용한 물류사업을 적극 추진해 다양한 생활 물류 서비스를 제공하겠다"고 말했다. 됐다. 이달 중 법령 개정이 확정되면 차량기지를 이용한 물류 수송 서비스가 가능하다. 도시철도 기반의 물류 플랫폼 조성사업을 진행하고 있다. 그 일환으로 지난 11월부터 2호선 홍대입구역에 캐리어 등 화물을 보관할 수 있는 유인 보관소 운영을 시작했다. 추가로 공항과 숙소로 캐리어를 배송하는 서비스를 이달 중순 개시를 목표로 준비 중이다.
http://biz.chosun.com/site/data/html_dir/2019/03/08/2019030802532.html?utm_source=bigkinds&utm_medium=original&utm_campaign=biz
<class 'str'>

http://news.mk.co.kr/newsRead.php?year=2018&no=549363
<class 'str'>
CJ대한통운은 매년 큰 성장세를 보이는 택배산업을 기반으로 양질의 일자리를 지속 창출하고 일자리 수혜대상을 노인뿐 아니라 경력단절여성, 장애인 등 취업 취약계층으로까지 확대해 나갈 계획이다.디지털뉴스국 이상규 기자, 무단전재 및 재배포 금지	nge the World) 50'에 국내 기업 최초로 선정된 바 있다. 

In [12]:
#Export dataframe if necessary

df_news.to_excel("df_news_updated.xlsx")

In [ ]:
#Adjustment
df_news['main_content'] = df_news['main_content'].str.replace(r'[^A-Za-z0-9가-힣 ]', '')

  
  
  
  
  
## Reference Code for Individual Media Source  (Legacy; No Longer Updated)

### 한겨례

In [ ]:
import urllib.request
from bs4 import BeautifulSoup

def contents_hankyoreh():
    
    #샘플 기사 URL
    list_url = "https://www.hani.co.kr/arti/politics/politics_general/1038853.html"
    
    url = urllib.request.Request(list_url)
    res = urllib.request.urlopen(url).read().decode("utf-8")
    #print(res)
    
    soup = BeautifulSoup(res, "html.parser")
    params1 = []
    params2 = []
    
    for link1, link2 in zip(soup.find_all('p', class_="date-time"), soup.find_all('div', class_="text")):
        params1.append(link1.get_text())
        params2.append(link2.get_text())
        
    for i1, i2 in zip(params1, params2):
        #print(i1.strip(), end=' ')
        print(i2.strip())
        
contents_hankyoreh()
    

### 한국경제

In [ ]:
#한국경제와 같은 경우 

import re
import urllib.request
from bs4 import BeautifulSoup

def cleanhtml(raw_html):
    cleanr = re.compile('<.*?>|\s{2}|\n')
    cleantext = re.sub(cleanr, '', raw_html)
    return cleantext

def contents_hankyung():
    
    #샘플 기사 URL
    list_url = "https://www.hankyung.com/finance/article/2021122646691"
    
    url = urllib.request.Request(list_url, headers={'User-Agent': 'Custom'}) #
    res = urllib.request.urlopen(url).read().decode("utf-8")
    
    soup = BeautifulSoup(res, "html.parser")
    
    content_obj = soup.find_all('div', id="articletxt")
    content = cleanhtml(str(content_obj))
    return content
        

contents_hankyung()
    

In [ ]:
        #한국경제
        elif 'hankyung' in url:
            headers = {'User-Agent':'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.88 Safari/537.36'}
            url = requests.get(url, headers=headers)

            soup = BeautifulSoup(url.content.decode('euc-kr', 'replace'), "html.parser", from_encoding='utf-8')
    
            content_obj = soup.find_all('div', id="articletxt")
            content = clean_html(str(content_obj))

### 경향신문

In [ ]:
#샘플 기사 URL
list_url = 'https://www.khan.co.kr/national/national-general/article/202204142115005'

def contents_kyunghyang(list_url):
    
    url = requests.get(list_url, headers={'User-Agent': 'Custom'})

    soup = BeautifulSoup(url.text, "html.parser")

    content_obj = soup.find_all('p', class_="content_text")

    content = cleanhtml(str(content_obj))
    return content

contents_kyunghyang(list_url)

### 동아일보

In [ ]:
list_url = 'https://www.donga.com/news/article/all/20220404/112693737/1'

def contents_donga(list_url):
    
    url = requests.get(list_url, headers={'User-Agent': 'Custom'})

    soup = BeautifulSoup(url.text, "html.parser")

    content_obj = soup.find_all('div', class_="article_txt")

    content = cleanhtml(str(content_obj))
    return content

contents_donga(list_url)

### 중앙일보

In [ ]:
list_url = 'https://news.joins.com/article/2137057'

def contents_joongang(list_url):
    
    url = requests.get(list_url, headers={'User-Agent': 'Custom'})

    soup = BeautifulSoup(url.text, "html.parser")

    content_obj = soup.find_all('div', class_="article_body")

    content = cleanhtml(str(content_obj))
    return content

contents_joongang(list_url)

### 매일경제

In [ ]:
import bs4
list_url = 'https://www.mk.co.kr/news/stock/view/2022/04/339384/'

def contents_maeil(list_url):
    
    url = requests.get(list_url, headers={'User-Agent': 'Custom'})

    soup = BeautifulSoup(url.text, "html.parser", from_encoding='')
    soup_alt = bs4.BeautifulSoup(url.content.decode('euc-kr', 'replace'), "html.parser")

    content_obj = soup_alt.find_all('div', class_="art_txt")

    content = clean_html(str(content_obj))
    return content

contents_maeil(list_url)

### 조선일보

In [ ]:
!pip install selenium

In [ ]:
#조선일보 같은 경우 셀레니움 패키지를 사용

import re
import requests
from bs4 import BeautifulSoup
import urllib.request
import selenium
from selenium import webdriver

options = webdriver.ChromeOptions()
options.add_argument('--headless')
options.add_argument('--no-sandbox')
options.add_argument('--disable-dev-shm-usage')

#driver = webdriver.Chrome(ChromeDriverManager().install())

list_url = 'https://www.chosun.com/economy/stock-finance/2021/12/10/OYYDOUAR35HZHBIOO5YAL4XTD4/?utm_source=bigkinds&utm_medium=original&utm_campaign=news'

content_obj = []

#Legacy Component
def contents_chosun(list_url):
    
    url = requests.get(list_url, headers={'User-Agent': 'Custom'})

    soup = BeautifulSoup(url.text, "html.parser")
    print(soup)
    content_obj = soup.find_all('p')
    print(content_obj)
    
    content = clean_html(str(content_obj))
    
    if soup.select_one('#text'):
        soup.dl.extract()
        news_article = soup.select_one('#article').text
        print(news_article)
    
#    for tag in soup.select('#text'):
#        print(tag.text)
#        write_ws.append([tag.text])
    
#    content = clean_html(str(content_obj))
    return content

contents_chosun(list_url)

In [ ]:
#셀레니윰을 통한 조선일보 크롤링 접근

from selenium import webdriver
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.common.by import By
import time

import pandas as pd
from selenium.common.exceptions import NoSuchElementException

list_url = 'https://www.chosun.com/economy/stock-finance/2021/12/10/OYYDOUAR35HZHBIOO5YAL4XTD4/?utm_source=bigkinds&utm_medium=original&utm_campaign=news'

content = []


#Selenium Component
driver = webdriver.Chrome(executable_path='/Users/ohikendoit/chromedriver', options=options)
driver.get(list_url)

driver.implicitly_wait(time_to_wait=5)
print(driver)

#more = driver.find_element_by_id('load-more-stories')

#for _ in range(120):
#    more.click()
#    time.sleep(1)
    
#selector = '#artwrapper > div > figure > div > div > div'
#a = driver.find_element(selector)

try:
    content_section = driver.find_element('//*[@id="fusion-app"]/div[1]/div[2]/div/section/article/section')
    p = content_section.find_elements('p')
    temp = []
    for item in p:
        temp.append(item.text)
    content.append('\n'.join(temp))
except:
    content.append(pd.NA)

driver.close()

## 셀레니움을 통한 조선일보 크롤링 구현

In [ ]:
from selenium import webdriver
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.common.by import By
import time
import pandas as pd
from selenium.common.exceptions import NoSuchElementException

In [ ]:
driver = webdriver.Chrome(executable_path='/Users/ohikendoit/chromedriver', options=options)
try:
    driver.get("https://www.google.com/")
except Exception as e:
    print(e.message)

In [ ]:
driver.get("https://www.google.com/")

In [ ]:
start_date = '20200501'
end_date = '20200502'
paper = 1023

num = 1
while True:
    driver.get(f'https://search.naver.com/search.naver?where=news&query=%EC%A7%80%EC%97%AD%ED%99%94%ED%8F%90&sm=tab_opt&sort=0&photo=0&field=0&pd=3&ds={start_date[0:4]}.{start_date[4:6]}.{start_date[6:]}&de={end_date[0:4]}.{end_date[4:6]}.{end_date[6:]}&docid=&related=0&mynews=1&office_type=1&office_section_code=1&news_office_checked={paper}&nso=so%3Ar%2Cp%3Afrom{start_date}to{end_date},a:all&start={num}')
    time.sleep(3)
    
    try:
        ul = driver.find_element(By.CSS_SELECTOR, '#main_pack > section > div > div.group_news > ul')
    except NoSuchElementException:
        print("Not exist paper")
        break
    lis = ul.find_elements(By.CLASS_NAME, 'li') #The previous approach has been depreciated.
    
    check = False
    
    for li in lis:
        tmp = li.get_attribute('id')
        tmp_url = driver.find_element(By.CSS_SELECTOR, f'#{tmp} > div > div > a').get_attribute("href")
        if tmp_url in url_list:
            check = True
            break
        url_list.append(tmp_url)
        
    if check:
        break
        
    num += 10

In [ ]:
url_list = ['https://biz.chosun.com/site/data/html_dir/2020/04/23/2020042302274.html?utm_source=bigkinds&utm_medium=original&utm_campaign=biz']

In [ ]:
for url in url_list:
    driver.get(url)
    time.sleep(1)
    content = driver.find_element_by_xpath('//*[@id="fusion-app"]/div[1]/div[2]/div/section/article/section').text
    print(content)
    
    print('='*30)
    print('='*30)